# Experiment Notebook: Compounding Yields for Pool Validators (Model Extension 5 - WIP)

# Table of Contents
* [Experiment Summary](#Experiment-Summary)
* [Experiment Assumptions](#Experiment-Assumptions)
* [Experiment Setup](#Experiment-Setup)
* [Analysis 1: Extended Time-domain](#Analysis-1:-Extended-Time-domain)
* [Analysis 2: Sweep of Pool Size](#Analysis-2:-Sweep-of-Pool-Size)

# Experiment Summary 

Each discrete validator requires a 32 ETH deposit when initialized. A validator's effective balance – the value used to calculate validator rewards – is a maximum of 32 ETH. Any rewards a validator earns above and beyond the 32 ETH requirement do not contribute to their yields until they accrue an additional 32 ETH and create another validator instance. This prevents a solo validator from reinvesting their yields to receive compound interest.

On the other hand, stakers that utilise validator pools, on exchanges for example, can compound their returns by pooling the returns of multiple validators to initialize another validator with 32 ETH. The pooling of returns and initialization of a shared validator effectively results in compound interest for those utilising staking pools, potentially resulting in much higher yields, especially over longer periods of time, than that of solo / distributed validators.

The following experiment notebook investigates ...


# Experiment Assumptions

 
* AVG Pool Size captures the mean pool size accross all pool environments.
* Because pool sizes are captured as an average, new shared validator instances are initialised simultaneously across pools leading to sudden 'jumps' in new shared validator instances as pools accrue the target validator stake ammount at the same time. In reality, jumps such as these would not occur in this manner due to variations in pool sizes across different pool validator environments.
* The current implementation assumes all pool validators engage in pool yield compounding. The model could implement a parameter accounting for the fraction of validator pools engaging in pool compounding once more data is known.

# Experiment Setup

We begin with several experiment-notebook-level preparatory setup operations:

* Import relevant dependencies
* Import relevant experiment templates
* Create copies of experiments
* Configure and customize experiments 

Analysis-specific setup operations are handled in their respective notebook sections.

In [53]:
# Import the setup module:
# * sets up the Python path
# * runs shared notebook configuration methods, such as loading IPython modules
import setup

import copy
import logging
import numpy as np
import pandas as pd
import plotly.express as px

import experiments.notebooks.visualizations as visualizations
from experiments.run import run
from experiments.utils import display_code
from model.types import Stage
from model.system_parameters import validator_environments


time: 26.8 ms (started: 2021-10-27 12:15:30 +02:00)


In [54]:
# Enable/disable logging
logger = logging.getLogger()
logger.disabled = False

time: 21.6 ms (started: 2021-10-27 12:15:30 +02:00)


In [55]:
# Import experiment templates
import experiments.templates.extended_time_horizon as extended_time_horizon
import experiments.templates.pool_size_sweep_analysis as pool_size_sweep_analysis

time: 22.4 ms (started: 2021-10-27 12:15:30 +02:00)


# Analysis 1: Extended Time-domain

Simulate the model over a 10 year period and plot relevent metrics. 

In [56]:
experiment = extended_time_horizon.experiment
simulation_1 = copy.deepcopy(extended_time_horizon.experiment.simulations[0])

time: 27.7 ms (started: 2021-10-27 12:15:30 +02:00)


In [57]:
# Experiment configuration:

normal_adoption = simulation_1.model.params['validator_process'][0](_run=None, _timestep=None)


simulation_1.model.params.update({
    # New validators per epoch
    "stage": [Stage.ALL],
    #"validator_process": [lambda _run, _timestep: normal_adoption * 1],
    "avg_pool_size": [100, 3000],
    "eth_price_process": [lambda _run, _timestep: 3000],
})


time: 27.8 ms (started: 2021-10-27 12:15:30 +02:00)


In [58]:
# Experiment execution
df_1, exceptions = run(simulation_1)

2021-10-27 12:15:30,961 - root - INFO - Running experiment
2021-10-27 12:15:30,963 - root - INFO - Starting simulation 0 / run 0 / subset 0
2021-10-27 12:15:31,169 - root - INFO - Starting simulation 0 / run 0 / subset 1
2021-10-27 12:15:31,365 - root - INFO - Experiment complete in 0.4036400318145752 seconds
2021-10-27 12:15:31,366 - root - INFO - Post-processing results
2021-10-27 12:15:32,464 - root - INFO - Post-processing complete in 1.0982489585876465 seconds
time: 1.53 s (started: 2021-10-27 12:15:30 +02:00)


In [59]:
df_1.query("timestep < 1020").validator_pools_profits

1       [0.0, 0.0, 235078.4387813174, 29418.1842785184...
2       [0.0, 0.0, 235078.4387813174, 29418.1842785184...
3       [0.0, 0.0, 235078.4387813174, 29418.1842785184...
4       [0.0, 0.0, 235078.4387813174, 29418.1842785184...
5       [0.0, 0.0, 235078.4387813174, 29418.1842785184...
                              ...                        
1025    [0.0, 0.0, 3503.1501853525406, 1562.4161797784...
1026    [0.0, 0.0, 3503.1501853525406, 1562.4161797784...
1027    [0.0, 0.0, 3503.1501853525406, 1562.4161797784...
1028    [0.0, 0.0, 3503.1501853525406, 1562.4161797784...
1029    [0.0, 0.0, 3503.1501853525406, 1562.4161797784...
Name: validator_pools_profits, Length: 1028, dtype: object

time: 46.7 ms (started: 2021-10-27 12:15:32 +02:00)


In [60]:
#df_1.query("shared_validator_instances > 0")
#pd.set_option("display.max_columns", None)
df_1

stage                  timestamp  eth_price    eth_supply  eth_staked  \
1       3.0 2021-10-27 11:59:27.433286     3000.0  1.181783e+08   8158432.0   
2       3.0 2021-11-03 11:59:27.433286     3000.0  1.182607e+08   8309632.0   
3       3.0 2021-11-10 11:59:27.433286     3000.0  1.183432e+08   8460832.0   
4       3.0 2021-11-17 11:59:27.433286     3000.0  1.184258e+08   8612032.0   
5       3.0 2021-11-24 11:59:27.433286     3000.0  1.185085e+08   8763232.0   
...     ...                        ...        ...           ...         ...   
1025    4.0 2031-07-30 11:59:27.433286     3000.0  1.185459e+08  88656288.0   
1026    4.0 2031-08-06 11:59:27.433286     3000.0  1.185515e+08  88818304.0   
1027    4.0 2031-08-13 11:59:27.433286     3000.0  1.185572e+08  88980352.0   
1028    4.0 2031-08-20 11:59:27.433286     3000.0  1.185630e+08  89142400.0   
1029    4.0 2031-08-27 11:59:27.433286     3000.0  1.185688e+08  89302880.0   

      supply_inflation  network_issuance  pow_issuance  \
1             0.036390      82363.188351     60.122793   
2             0.036402      82448.397908     60.122793   
3             0.036408      82518.298489     60.122793   
4             0.036418      82597.876258     60.122793   
5             0.036426      82674.750768     60.122793   
...                ...               ...           ...   
1025          0.002459       5586.185747      0.000000   
1026          0.002481       5637.842387      0.000000   
1027          0.002504       5689.509230      0.000000   
1028          0.002527       5741.176074      0.000000   
1029          0.002549       5792.342981      0.000000   

      number_of_validators_in_activation_queue  \
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          0.0   
5                                          0.0   
...                                        ...   
1025                                       0.0   
1026                                       0.0   
1027                                       0.0   
1028                                       0.0   
1029                                       0.0   

           validators_in_activation_queue  average_effective_balance  \
1     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
2     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
3     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
4     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
5     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
...                                   ...                        ...   
1025  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
1026  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
1027  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
1028  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   
1029  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]               3.200000e+10   

      number_of_active_validators  number_of_awake_validators  \
1                        254951.0                    250226.0   
2                        259676.0                    254951.0   
3                        264401.0                    259676.0   
4                        269126.0                    264401.0   
5                        273851.0                    269126.0   
...                           ...                         ...   
1025                    2770509.0                   2765714.0   
1026                    2775572.0                   2770509.0   
1027                    2780636.0                   2775572.0   
1028                    2785700.0                   2780636.0   
1029                    2790715.0                   2785700.0   

      validator_uptime  base_reward  validating_rewards  validating_penalties  \
1                 0.98   3568320

time: 281 ms (started: 2021-10-27 12:15:32 +02:00)


In [61]:
df_1.pool_staas_validator_count

1        68837.0
2        70113.0
3        71389.0
4        72665.0
5        73941.0
          ...   
1025    804138.0
1026    805682.0
1027    807227.0
1028    808772.0
1029    810318.0
Name: pool_staas_validator_count, Length: 1028, dtype: float32

time: 23.4 ms (started: 2021-10-27 12:15:32 +02:00)


## Visualizations

#### To Do:
* Create / use visualization plots in __init__.py
* Label all x-axis time as Date


In [62]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_shared_validators', 'pool_hardware_shared_validators', 'pool_cloud_shared_validators', 'diy_hardware_shared_validators', 'diy_cloud_shared_validators'],
    animation_frame='avg_pool_size'
)

time: 330 ms (started: 2021-10-27 12:15:32 +02:00)


In [63]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_pools_profit', 'pool_hardware_pools_profit', 'pool_cloud_pools_profit', 'diy_hardware_pools_profit', 'diy_cloud_pools_profit'],
    animation_frame='avg_pool_size'
)

time: 350 ms (started: 2021-10-27 12:15:33 +02:00)


In [64]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_validator_count', 'pool_hardware_validator_count', 'pool_cloud_validator_count', 'diy_hardware_validator_count', 'diy_cloud_validator_count'],
    animation_frame='avg_pool_size'
)

time: 355 ms (started: 2021-10-27 12:15:33 +02:00)


In [17]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_eth_staked', 'pool_hardware_eth_staked', 'pool_cloud_eth_staked', 'diy_hardware_eth_staked', 'staas_full_eth_staked'],
    animation_frame='avg_pool_size'
)

time: 388 ms (started: 2021-10-27 12:00:53 +02:00)


In [18]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_profit', 'pool_hardware_profit', 'pool_cloud_profit', 'diy_hardware_profit', 'diy_cloud_profit'],
    animation_frame='avg_pool_size'
)

time: 368 ms (started: 2021-10-27 12:00:54 +02:00)


In [19]:


px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_staker_profit_yields_pct', 'pool_hardware_staker_profit_yields_pct', 'pool_cloud_staker_profit_yields_pct', 'diy_hardware_staker_profit_yields_pct'],
    animation_frame='avg_pool_size'
)


time: 292 ms (started: 2021-10-27 12:00:54 +02:00)


# Analysis 2: Sweep of Pool Size

Phase-space analysis showing metrics as a function of the average pool size for pool validators using pool compounding.

* In order to accurately account for the compounding of pool validator yeilds over time, we first simulate the model over the desired time-horizon.
* Then, we perform a phase-space analysis at the desired timestep (e.g. at year 10)


In [20]:
# Analysis-specific setup

time: 23 ms (started: 2021-10-27 12:00:54 +02:00)


In [21]:
# Fetch the pool-size sweep analysis experiment
experiment = pool_size_sweep_analysis.experiment
# Create a copy of the experiment simulation
simulation_2 = copy.deepcopy(experiment.simulations[0])

time: 26.6 ms (started: 2021-10-27 12:00:54 +02:00)


In [22]:
# Experiment configuration

normal_adoption = simulation_2.model.params['validator_process'][0](_run=None, _timestep=None)

simulation_2.model.params.update({
    "validator_process": [lambda _run, _timestep: normal_adoption], # New validators per epoch
    "stage": [Stage.ALL], 
    "eth_price_process": [lambda _run, _timestep: 3000],
    
})


# Select the year to simulate to:
YEAR = 5
TIMESTEP_ANALYSIS = YEAR * 12 # convert year to month

time: 24.4 ms (started: 2021-10-27 12:00:54 +02:00)


In [23]:
# Experiment execution
df_2, exceptions = run(simulation_2)

2021-10-27 12:00:54,797 - root - INFO - Running experiment
2021-10-27 12:00:54,800 - root - INFO - Starting simulation 0 / run 0 / subset 0
2021-10-27 12:00:54,852 - root - INFO - Starting simulation 0 / run 0 / subset 1
2021-10-27 12:00:54,905 - root - INFO - Starting simulation 0 / run 0 / subset 2
2021-10-27 12:00:54,956 - root - INFO - Starting simulation 0 / run 0 / subset 3
2021-10-27 12:00:55,005 - root - INFO - Starting simulation 0 / run 0 / subset 4
2021-10-27 12:00:55,055 - root - INFO - Starting simulation 0 / run 0 / subset 5
2021-10-27 12:00:55,108 - root - INFO - Starting simulation 0 / run 0 / subset 6
2021-10-27 12:00:55,164 - root - INFO - Starting simulation 0 / run 0 / subset 7
2021-10-27 12:00:55,208 - root - INFO - Starting simulation 0 / run 0 / subset 8
2021-10-27 12:00:55,255 - root - INFO - Starting simulation 0 / run 0 / subset 9
2021-10-27 12:00:55,302 - root - INFO - Starting simulation 0 / run 0 / subset 10
2021-10-27 12:00:55,349 - root - INFO - Starting 

2021-10-27 12:00:59,568 - root - INFO - Experiment complete in 4.76927638053894 seconds
2021-10-27 12:00:59,568 - root - INFO - Post-processing results
2021-10-27 12:01:11,348 - root - INFO - Post-processing complete in 11.780224800109863 seconds
time: 16.6 s (started: 2021-10-27 12:00:54 +02:00)


## Visualizations

#### To Do
* Set time analysis point in labels / headings

In [24]:
# To plot a specific point in time without having to re-run the simulation, 
# set TIMESTEP_ANALYSIS below and re-run the following cells.

YEAR = 10
TIMESTEP_ANALYSIS = YEAR * 12  # convert year to month

time: 25.8 ms (started: 2021-10-27 12:01:11 +02:00)


In [25]:
visualizations.plot_staker_profit_yields_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 54.5 ms (started: 2021-10-27 12:01:11 +02:00)


In [26]:
visualizations.plot_profit_yields_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 49.3 ms (started: 2021-10-27 12:01:11 +02:00)


In [27]:
visualizations.plot_profit_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 48.1 ms (started: 2021-10-27 12:01:11 +02:00)


In [28]:
visualizations.plot_eth_staked_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 56 ms (started: 2021-10-27 12:01:11 +02:00)
